In [1]:
%pip install sqlalchemy psycopg2-binary

   ---------------------------------------- 0.0/2.1 MB ? eta -:--:--
   ---------------------------------------- 2.1/2.1 MB 29.6 MB/s  0:00:00
   ---------------------------------------- 0.0/1.2 MB ? eta -:--:--
   ---------------------------------------- 1.2/1.2 MB 29.1 MB/s  0:00:00

   ------------- -------------------------- 1/3 [greenlet]
   ------------- -------------------------- 1/3 [greenlet]
   ------------- -------------------------- 1/3 [greenlet]
   -------------------------- ------------- 2/3 [sqlalchemy]
   -------------------------- ------------- 2/3 [sqlalchemy]
   -------------------------- ------------- 2/3 [sqlalchemy]
   -------------------------- ------------- 2/3 [sqlalchemy]
   -------------------------- ------------- 2/3 [sqlalchemy]
   -------------------------- ------------- 2/3 [sqlalchemy]
   -------------------------- ------------- 2/3 [sqlalchemy]
   -------------------------- ------------- 2/3 [sqlalchemy]
   -------------------------- ------------- 2/3 

In [ ]:
import pandas as pd
from sqlalchemy import create_engine
import traceback

db_type = 'postgresql'
db_driver = 'psycopg2'
db_user = 'carfin_admin'
db_password = 'carfin_secure_password_2025'
db_host = 'carfin-db.cbkayiqs4div.ap-northeast-2.rds.amazonaws.com'
db_port = '5432'
db_name = 'carfin'

schema = 'public'
table_name = 'vehicles'

try:

    connection_string = f"{db_type}+{db_driver}://{db_user}:{db_password}@{db_host}:{db_port}/{db_name}"

    # 데이터베이스 연결 엔진
    engine = create_engine(connection_string)

    # SQL 쿼리b
    sql_query = f"SELECT * FROM {schema}.{table_name}"

    # 쿼리 실행하여 데이터를 DataFrame으로 로드
    df = pd.read_sql(sql_query, engine)

    print("✅ 데이터베이스 연결 및 데이터 불러오기 성공!")
    print(f"총 {len(df)}개의 행을 불러왔습니다.")
    print("\n--- 데이터 미리보기 (상위 5개) ---")
    print(df.head())

except Exception as e:
    print(" 오류가 발생")

    traceback.print_exc()

✅ 데이터베이스 연결 및 데이터 불러오기 성공!
총 85308개의 행을 불러왔습니다.

--- 데이터 미리보기 (상위 5개) ---
  vehicleid      carseq vehicleno platform origin cartype manufacturer  \
0       [1]  [40280246]  359마6078    encar     국산      경차           기아   
1       [2]  [40539834]  196주2722    encar     국산      경차           기아   
2       [3]  [40536828]   30보7029    encar     국산      경차    쉐보레(GM대우)   
3       [4]  [40523706]   65오0942    encar     국산      경차    쉐보레(GM대우)   
4       [5]  [40524639]  177거9036    encar     국산      경차           기아   

         model generation       trim  ... colorname modelyear  \
0   모닝 어반 (JA)       스탠다드  (세부등급 없음)  ...        흰색    [2021]   
1    더 뉴 기아 레이       시그니처       None  ...        흰색    [2023]   
2          스파크         LT        기본형  ...       분홍색    [2012]   
3    더 넥스트 스파크        LTZ       None  ...        흰색    [2016]   
4  올 뉴 모닝 (JA)        디럭스       None  ...        흰색    [2017]   

  firstregistrationdate  distance   price originprice selltype location  \
0            [2

In [4]:
print('--데이터 정보--')
df.info()

print('\n결측치 개수')
print(df.isnull().sum())

--데이터 정보--
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 85308 entries, 0 to 85307
Data columns (total 22 columns):
 #   Column                 Non-Null Count  Dtype 
---  ------                 --------------  ----- 
 0   vehicleid              85308 non-null  object
 1   carseq                 85308 non-null  object
 2   vehicleno              85308 non-null  object
 3   platform               85308 non-null  object
 4   origin                 85308 non-null  object
 5   cartype                85308 non-null  object
 6   manufacturer           85308 non-null  object
 7   model                  85308 non-null  object
 8   generation             85308 non-null  object
 9   trim                   35292 non-null  object
 10  fueltype               85307 non-null  object
 11  transmission           85306 non-null  object
 12  colorname              85308 non-null  object
 13  modelyear              85307 non-null  object
 14  firstregistrationdate  77551 non-null  object
 15  distance

In [5]:
# 데이터 전처리
# trim 칼럼 -> null 값: 50016개
# fueltype 칼럼 -> null 값: 1개
# transmission 칼럼 -> null 값이: 2개
# modelyear 칼럼 -> null 값: 1개
# firstregistrationdate 칼럼 -> null 값: 7757개
# originprice 칼럼 -> null 값: 4661개
# photo 칼럼 -> null 값: 68개

# 'trim' 컬럼: '정보없음'으로 대체
df['trim'].fillna('정보없음', inplace=True)

# 개수가 적은 결측치 행들 삭제
df.dropna(subset=['photo', 'location', 'transmission', 'fueltype', 'modelyear'], inplace=True)

# 'originprice'와 'modelyear'를 숫자 타입으로 변환 (대체를 위해 선행)
# 숫자로 바꿀 수 없는 값은 강제로 결측(NaN)으로
df['originprice'] = pd.to_numeric(df['originprice'], errors='coerce')
df['modelyear'] = pd.to_numeric(df['modelyear'], errors='coerce')

# 'originprice': 그룹별 중앙값으로 대체
df['originprice'] = df.groupby(['manufacturer', 'model', 'generation'])['originprice'].transform(lambda x: x.fillna(x.median()))
# 그룹 중앙값으로도 채워지지 않는 나머지 소수는 전체 중앙값으로 채우거나 삭제
df['originprice'].fillna(df['originprice'].median(), inplace=True)

# 'firstregistrationdate': 연식 기반으로 대체
df['firstregistrationdate'].fillna(df['modelyear'].astype(str).str.split('.').str[0] + '-01-01', inplace=True)

#  최종 확인 
print("--- 결측치 처리 후 남은 결측치 개수 ---")
print(df.isnull().sum())

c:\Users\opgrs\anaconda3\envs\final_project\Lib\site-packages\numpy\lib\_nanfunctions_impl.py:1214: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
c:\Users\opgrs\anaconda3\envs\final_project\Lib\site-packages\numpy\lib\_nanfunctions_impl.py:1214: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
c:\Users\opgrs\anaconda3\envs\final_project\Lib\site-packages\numpy\lib\_nanfunctions_impl.py:1214: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
c:\Users\opgrs\anaconda3\envs\final_project\Lib\site-packages\numpy\lib\_nanfunctions_impl.py:1214: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
c:\Users\opgrs\anaconda3\envs\final_project\Lib\site-packages\numpy\lib\_nanfunctions_impl.py:1214: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
c:\Users\opgrs\anaconda3\envs\final

--- 결측치 처리 후 남은 결측치 개수 ---
vehicleid                    0
carseq                       0
vehicleno                    0
platform                     0
origin                       0
cartype                      0
manufacturer                 0
model                        0
generation                   0
trim                         0
fueltype                     0
transmission                 0
colorname                    0
modelyear                85231
firstregistrationdate        0
distance                     0
price                        0
originprice              85231
selltype                     0
location                     0
detailurl                    0
photo                        0
dtype: int64


C:\Users\opgrs\AppData\Local\Temp\ipykernel_18360\3020563226.py:27: FutureWarning: A value is trying to be set on a copy of a DataFrame or Series through chained assignment using an inplace method.
The behavior will change in pandas 3.0. This inplace method will never work because the intermediate object on which we are setting values always behaves as a copy.

For example, when doing 'df[col].method(value, inplace=True)', try using 'df.method({col: value}, inplace=True)' or df[col] = df[col].method(value) instead, to perform the operation inplace on the original object.


  df['firstregistrationdate'].fillna(df['modelyear'].astype(str).str.split('.').str[0] + '-01-01', inplace=True)


In [6]:
# 데이터 클리닝: 숫자 외 문자 제거
# moodel year: 년, 년식, 공백 등 제거
df['modelyear'] = df['modelyear'].astype(str).str.replace(r'[^0-9]','',regex=True)
# origin price: 만원, , , 공백 등 제거
df['originprice'] = df['originprice'].astype(str).str.replace(r'[^0-9]','',regex=True)


# 위에서 문자를 제거하면 빈 문자열이 생길 수 있으므로 '0'으로 바꾼 후 숫자로 변환
df.loc[df['originprice'] == '','originprice'] = '0'
df['originprice'] = df['originprice'].astype(float)
# 가격이 0인 값은 다시 결측치로 처리
df['originprice'].replace(0,pd.NA, inplace=True)


# 'trim' 컬럼: '정보없음'으로 대체
df['trim'].fillna('정보없음', inplace=True)

# 개수가 매우 적은 결측치 행들 삭제
df.dropna(subset=['photo', 'location', 'transmission', 'fueltype'], inplace=True)

# 'originprice': 그룹별 중앙값으로 대체
# 'transform'은 그룹별 계산 결과를 원래 df의 인덱스에 맞게 반환해줍니다.
df['originprice'] = df.groupby(['manufacturer', 'model', 'generation'])['originprice'].transform(lambda x: x.fillna(x.median()))
# 그룹 중앙값으로도 채워지지 않는 나머지는 전체 중앙값으로 채웁니다.
df['originprice'].fillna(df['originprice'].median(), inplace=True)

# 'firstregistrationdate': 연식 기반으로 대체
df['firstregistrationdate'].fillna(df['modelyear'].astype(str) + '-01-01', inplace=True)


# --- 최종 확인 ---
print("--- 수정된 코드로 전처리 후 남은 결측치 개수 ---")
print(df.isnull().sum())

C:\Users\opgrs\AppData\Local\Temp\ipykernel_18360\2724182721.py:12: FutureWarning: A value is trying to be set on a copy of a DataFrame or Series through chained assignment using an inplace method.
The behavior will change in pandas 3.0. This inplace method will never work because the intermediate object on which we are setting values always behaves as a copy.

For example, when doing 'df[col].method(value, inplace=True)', try using 'df.method({col: value}, inplace=True)' or df[col] = df[col].method(value) instead, to perform the operation inplace on the original object.


  df['originprice'].replace(0,pd.NA, inplace=True)
C:\Users\opgrs\AppData\Local\Temp\ipykernel_18360\2724182721.py:16: FutureWarning: A value is trying to be set on a copy of a DataFrame or Series through chained assignment using an inplace method.
The behavior will change in pandas 3.0. This inplace method will never work because the intermediate object on which we are setting values always behaves as a copy.

For e

--- 수정된 코드로 전처리 후 남은 결측치 개수 ---
vehicleid                    0
carseq                       0
vehicleno                    0
platform                     0
origin                       0
cartype                      0
manufacturer                 0
model                        0
generation                   0
trim                         0
fueltype                     0
transmission                 0
colorname                    0
modelyear                    0
firstregistrationdate        0
distance                     0
price                        0
originprice              85231
selltype                     0
location                     0
detailurl                    0
photo                        0
dtype: int64


In [7]:
print(df.head())

  vehicleid      carseq vehicleno platform origin cartype manufacturer  \
0       [1]  [40280246]  359마6078    encar     국산      경차           기아   
1       [2]  [40539834]  196주2722    encar     국산      경차           기아   
2       [3]  [40536828]   30보7029    encar     국산      경차    쉐보레(GM대우)   
3       [4]  [40523706]   65오0942    encar     국산      경차    쉐보레(GM대우)   
4       [5]  [40524639]  177거9036    encar     국산      경차           기아   

         model generation       trim  ... colorname modelyear  \
0   모닝 어반 (JA)       스탠다드  (세부등급 없음)  ...        흰색             
1    더 뉴 기아 레이       시그니처       정보없음  ...        흰색             
2          스파크         LT        기본형  ...       분홍색             
3    더 넥스트 스파크        LTZ       정보없음  ...        흰색             
4  올 뉴 모닝 (JA)        디럭스       정보없음  ...        흰색             

  firstregistrationdate  distance   price originprice selltype  location  \
0            [20210617]   [28088]   [990]         NaN       일반        경기   
1           

In [ ]:
# originprice 결측치 채우기
df['originprice'] = df.groupby(['manufacturer','model','generation'])['originprice'].transform(lambda x: x.fillna(x.median()))
# 결측치 개수
print(f"originprice 결측치: {df['originprice'].isnull().sum()}개")

c:\Users\opgrs\anaconda3\envs\final_project\Lib\site-packages\numpy\lib\_nanfunctions_impl.py:1214: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
c:\Users\opgrs\anaconda3\envs\final_project\Lib\site-packages\numpy\lib\_nanfunctions_impl.py:1214: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
c:\Users\opgrs\anaconda3\envs\final_project\Lib\site-packages\numpy\lib\_nanfunctions_impl.py:1214: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
c:\Users\opgrs\anaconda3\envs\final_project\Lib\site-packages\numpy\lib\_nanfunctions_impl.py:1214: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
c:\Users\opgrs\anaconda3\envs\final_project\Lib\site-packages\numpy\lib\_nanfunctions_impl.py:1214: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
c:\Users\opgrs\anaconda3\envs\final

originprice 결측치: 85231개


c:\Users\opgrs\anaconda3\envs\final_project\Lib\site-packages\numpy\lib\_nanfunctions_impl.py:1214: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
c:\Users\opgrs\anaconda3\envs\final_project\Lib\site-packages\numpy\lib\_nanfunctions_impl.py:1214: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
c:\Users\opgrs\anaconda3\envs\final_project\Lib\site-packages\numpy\lib\_nanfunctions_impl.py:1214: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
c:\Users\opgrs\anaconda3\envs\final_project\Lib\site-packages\numpy\lib\_nanfunctions_impl.py:1214: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
c:\Users\opgrs\anaconda3\envs\final_project\Lib\site-packages\numpy\lib\_nanfunctions_impl.py:1214: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
c:\Users\opgrs\anaconda3\envs\final

In [9]:
print(df.head())

  vehicleid      carseq vehicleno platform origin cartype manufacturer  \
0       [1]  [40280246]  359마6078    encar     국산      경차           기아   
1       [2]  [40539834]  196주2722    encar     국산      경차           기아   
2       [3]  [40536828]   30보7029    encar     국산      경차    쉐보레(GM대우)   
3       [4]  [40523706]   65오0942    encar     국산      경차    쉐보레(GM대우)   
4       [5]  [40524639]  177거9036    encar     국산      경차           기아   

         model generation       trim  ... colorname modelyear  \
0   모닝 어반 (JA)       스탠다드  (세부등급 없음)  ...        흰색             
1    더 뉴 기아 레이       시그니처       정보없음  ...        흰색             
2          스파크         LT        기본형  ...       분홍색             
3    더 넥스트 스파크        LTZ       정보없음  ...        흰색             
4  올 뉴 모닝 (JA)        디럭스       정보없음  ...        흰색             

  firstregistrationdate  distance   price originprice selltype  location  \
0            [20210617]   [28088]   [990]         NaN       일반        경기   
1           